# Experiment 2  

We evaluate how different **Train/Test Split Strategies** and **enforced workload orders** impact model performance and robustness:  

### **Train/Test Split Strategies**  
1. **Leave-One-Out Sampling**: For each query template, one instance is held out for testing while the rest are used for training.  
2. **Random Sampling**: The workload is split uniformly into train/test sets (e.g., 80/20) across all queries.  
3. **Template-Based Splitting**: Training and testing sets are partitioned by query templates, ensuring no overlap.  

[![Train/Test Split Visualization](https://i.postimg.cc/ncdg9W6w/image-2-1.png)](https://postimg.cc/hfdpH249)  

### **Enforced Workload Orders (Training Phase)**  
1. **Random Order**: Queries are shuffled randomly during training.  
2. **Ascending Complexity**: Queries are ordered by join complexity (simple → complex).  
3. **Ascending Latency (Worst-Case Order)**: Queries are sorted by PostgreSQL execution time (fastest → slowest).  

---  

## **Key Evaluation Metrics**  
- **Overall Workload Performance**: How optimizers perform under different split strategies and workload orders.  
- **Workload Robustness**: Whether performance fluctuates across repeated executions of the same queries with the same models.  

In [2]:
import os
import json
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
from collections import defaultdict
from ast import literal_eval

RANDOM_SPLIT_TEST_QUERIES = [
    '1c.sql', '2c.sql', '4b.sql', '4c.sql', '5c.sql', '6a.sql', '6c.sql', '6e.sql', '8b.sql', '8c.sql', '9c.sql',
    '11d.sql', '15a.sql', '17b.sql', '17e.sql', '18b.sql',
    '20a.sql', '21a.sql', '25c.sql', '28b.sql',
    '32b.sql', '33a.sql'
]

BASE_QUERY_SPLIT_TEST_QUERIES = [
    '2a.sql', '2b.sql', '2c.sql', '2d.sql',
    '7a.sql', '7b.sql', '7c.sql',
    '15a.sql', '15b.sql', '15c.sql', '15d.sql',
    '24a.sql', '24b.sql', 
    '25a.sql', '25b.sql', '25c.sql',
    '31a.sql', '31b.sql', '31c.sql',
]

LEAVE_ONE_OUT_SPLIT_TEST_QUERIES = [
    '1c.sql', '2a.sql', '3b.sql', '4a.sql', '5a.sql', '6b.sql', '7c.sql', '8c.sql', '9c.sql',
    '10b.sql', '11b.sql', '12c.sql', '13b.sql', '14a.sql', '15b.sql', '16c.sql', '17c.sql', '18b.sql', '19a.sql',
    '20c.sql', '21c.sql', '22b.sql', '23b.sql', '24a.sql', '25a.sql', '26c.sql', '27c.sql', '28a.sql', '29b.sql',
    '30a.sql', '31b.sql', '32b.sql', '33c.sql'
]

base_query_dir = '/data/hdd1/users/kmparmp/Learned-Optimizers-Benchmarking-Suite/experiments/experiment2/test/base_query'
random_split_query_dir = '/data/hdd1/users/kmparmp/Learned-Optimizers-Benchmarking-Suite/experiments/experiment2/test/random'
leave_one_out_query_dir = '/data/hdd1/users/kmparmp/Learned-Optimizers-Benchmarking-Suite/experiments/experiment2/test/leave_one_out'

query_dirs = {
    "base_query": base_query_dir,
    "random_split": random_split_query_dir,
    "leave_one_out": leave_one_out_query_dir
}

workload_orders = ["ascending_complexity", "ascending_latency", "random"]

# optimizers = ["Postgres", "BAO", "LOGER", "FASTgres", "LERO"]
optimizers = ["Postgres", "BAO", "LOGER", "FASTgres", "LERO", "NEO"]

## Overall Workload Performance

In [3]:
RUNS = 3

# Update your results collection code to also store planning time
results = defaultdict(lambda: {'execution_time': [], 'planning_time': []})

def read_postgres_times(query_path, run):
    file_path = os.path.join(query_path, f"classic_qep.json")
    if not os.path.exists(file_path):
        return None, None
    with open(file_path, 'r') as f:
        data = json.load(f)
    exec_time = float(data[0].get('Execution Time', 0))
    plan_time = float(data[0].get('Planning Time', 0))
    return exec_time / 1000, plan_time / 1000

def read_optimizer_times(query_path, query_name, optimizer, run):
    if optimizer == "LERO":
        result_file = os.path.join(query_path, optimizer, f"run{run}", f"{query_name}_plan.json")
    else:
        result_file = os.path.join(query_path, optimizer, f"run{run}", f"{query_name}_{optimizer.lower()}_plan.json")

    if not os.path.exists(result_file):
        # print("Fail lol")
        return None, None

    with open(result_file, 'r') as f:
        data = json.load(f)
        if optimizer == "BAO" and isinstance(data, list):
            data = data[1]

    # Execution time
    exec_time = data[0].get('Execution Time') if isinstance(data, list) else data.get('Execution Time')
    exec_time = float(exec_time) / 1000 if exec_time else None

    # Planning time
    if optimizer in ("BAO", "LERO"):
        plan_time = data[0].get('Planning Time') if isinstance(data, list) else data.get('Planning Time')
        plan_time = float(plan_time) / 1000 if plan_time else None
    else:
        metrics_file = os.path.join(query_path, optimizer, f"run{run}", f"{query_name}_{optimizer.lower()}_metrics.json")
        plan_time = None
        if os.path.exists(metrics_file):
            with open(metrics_file, 'r') as mf:
                metrics_data = json.load(mf)
            if optimizer in ("LOGER", "NEO"):
                plan_time = metrics_data.get('inference_time', 0)
            else:
                plan_time = metrics_data.get('forward_time', 0)
            plan_time = float(plan_time) if isinstance(plan_time, str) else plan_time

    return exec_time, plan_time

for query_type, dir in query_dirs.items():
    for workload_order in workload_orders:
        template_path = os.path.join(dir, workload_order)
        if not os.path.exists(template_path):
            print(f"Query path {template_path} does not exist.")
            continue

        for query_name in os.listdir(template_path):
            query_path = os.path.join(template_path, query_name)
            if not os.path.isdir(query_path):
                continue

            for optimizer in optimizers:
                exec_times, plan_times = [], []

                for run in range(1, RUNS + 1):
                    if optimizer == "Postgres":
                        exec_time, plan_time = read_postgres_times(query_path, run)
                        # print(f"Read Postgres times for {query_name} run {run}: exec_time={exec_time}, plan_time={plan_time}")
                    else:
                        exec_time, plan_time = read_optimizer_times(query_path, query_name, optimizer, run)

                    if exec_time is not None:
                        exec_times.append(exec_time)
                    if plan_time is not None:
                        plan_times.append(plan_time)

                results[(query_type, workload_order, query_name, optimizer)]['execution_time'].extend(exec_times)
                results[(query_type, workload_order, query_name, optimizer)]['planning_time'].extend(plan_times)

# Convert to DataFrame
df_data = []
for key, metrics in results.items():
    query_type, workload_order, query_name, optimizer = key
    for i in range(len(metrics['execution_time'])):
        df_data.append({
            'query_type': query_type,
            'workload_order': workload_order,
            'query_name': query_name,
            'optimizer': optimizer,
            'run': i+1,
            'execution_time': metrics['execution_time'][i],
            'planning_time': metrics['planning_time'][i]
        })

df = pd.DataFrame(df_data)

In [31]:
import matplotlib.pyplot as plt
import numpy as np
from matplotlib.colors import to_rgb, to_hex
import matplotlib.ticker as ticker

# Prepare the data - sum both metrics
grouped = df.groupby(['query_type', 'workload_order', 'optimizer']).sum().unstack()
plan_data = grouped['planning_time']
exec_data = grouped['execution_time']

# Define plot settings
query_types = {
    'leave_one_out': 'Leave One Out',
    'random_split': 'Random Split',
    'base_query': 'Base Query'
}

workload_orders = {
    'ascending_latency': 'Latency',
    'ascending_complexity': 'Complex.',
    'random': 'Random'
}

optimizers = ['Postgres', 'NEO', 'BAO', 'LOGER', 'FASTgres', 'LERO']
# optimizers = ['Postgres', 'BAO', 'LOGER', 'FASTgres', 'LERO']

# --- Color & pattern config ---
base_colors = {
    'Postgres': '#1f77b4',
    'NEO': '#ff7f0e',
    'BAO': '#2ca02c',
    'LOGER': '#d62728',
    'FASTgres': '#9467bd',
    'LERO': '#8c564b'
}

# Define patterns for each optimizer
patterns = {
    'Postgres': '',       # Solid (no hatch)
    'NEO': '//',       # Forward slashes
    'BAO': '\\\\',      # Backward slashes (backslashes must be escaped)
    'LOGER': '||',       # Vertical lines
    'FASTgres': '--',      # Horizontal lines
    'LERO': 'OO'        # Large circles
}

# Function to create lighter/darker shades
def adjust_lightness(color, amount=0.5):
    import colorsys
    try:
        c = colorsys.rgb_to_hls(*to_rgb(color))
        return to_hex(colorsys.hls_to_rgb(c[0], max(0, min(1, amount * c[1])), c[2]))
    except:
        return color

# Create the combined plot
plt.figure(figsize=(26, 14), dpi=600)  # Slightly wider figure to accommodate more optimizers
plt.rcParams['hatch.linewidth'] = 0.2
plt.rcParams.update({'font.size': 38})
# Generate x-axis labels and positions
x_labels = []
x_positions = []
pos = 0

n_optimizers = len(optimizers)
group_width = 0.95
bar_width = group_width / n_optimizers

# gap_between_query_types = 0.01  # adjust this for visible spacing

for q_i, query_type in enumerate(query_types):
    for workload_order in workload_orders:
        x_labels.append(workload_orders[workload_order])
        x_positions.append(pos + group_width/2)
        pos += group_width
    # pos += gap_between_query_types  # add gap after finishing one query_type group

x = np.arange(len(optimizers))

# --- Plot stacked bars for each group ---
for i, (query_type, workload_order) in enumerate([(qt, wo) for qt in query_types for wo in workload_orders]):
    bar_gap = 1.1
    bar_width = group_width / (n_optimizers * bar_gap)
    group_x = x_positions[i] - group_width/2 + bar_width/2 + x * bar_width
    
    for j, optimizer in enumerate(optimizers):
        base_color = base_colors[optimizer]
        light_color = adjust_lightness(base_color, 1.4)
        dark_color = adjust_lightness(base_color, 0.7)
        
        planning_times = plan_data.loc[(query_type, workload_order)][optimizer]
        execution_times = exec_data.loc[(query_type, workload_order)][optimizer]
        
        # Planning
        plt.bar(group_x[j], 
                planning_times, 
                width=bar_width, 
                color=light_color,
                edgecolor='black',
                hatch=patterns[optimizer],
                label=f"{optimizer} Plan." if i == 0 and j == 0 else "")
        
        # Execution
        plt.bar(group_x[j], 
                execution_times, 
                width=bar_width, 
                bottom=planning_times,
                color=dark_color,
                edgecolor='black',
                hatch=patterns[optimizer],
                label=f"{optimizer} Exec." if i == 0 and j == 0 else "")

# --- Custom legend ---
legend_elements = []
for optimizer in optimizers:
    base_color = base_colors[optimizer]
    light_color = adjust_lightness(base_color, 1.4)
    dark_color = adjust_lightness(base_color, 0.7)
    
    legend_elements.append(plt.Rectangle((0,0), 1, 1, 
                          fc=light_color, 
                          hatch=patterns[optimizer],
                          edgecolor='black',
                          label=f"{optimizer} Plan."))
    legend_elements.append(plt.Rectangle((0,0), 1, 1, 
                          fc=dark_color, 
                          hatch=patterns[optimizer],
                          edgecolor='black',
                          label=f"{optimizer} Exec."))

ax = plt.gca()

# --- Main x-axis: workload orders ---
ax.set_xticks(x_positions)
ax.set_xticklabels(x_labels, fontsize=38, rotation=0, ha='center')

# --- Secondary x-axis: query type group labels ---
secax = ax.secondary_xaxis('bottom')
secax.set_xticks([
    np.mean(x_positions[i*len(workload_orders):(i+1)*len(workload_orders)])
    for i in range(len(query_types))
])
secax.set_xticklabels([query_types[qt] for qt in query_types], fontsize=38, weight='bold')

# Push labels so they don’t overlap
secax.spines['bottom'].set_position(('outward', 45))
ax.tick_params(axis='x', which='major', pad=0)

# --- Legend ---
plt.legend(
    handles=legend_elements,
    loc='upper center',
    bbox_to_anchor=(0.5, 1.36),
    ncol=len(legend_elements)//2,
    fontsize=34,
    frameon=True,
    facecolor='white',
    edgecolor='black',
    fancybox=True,
    shadow=False,
    labelspacing=0.2,
    handletextpad=0.2, 
    columnspacing=0.6,
    handlelength=1.2
)

# --- Grid + formatting ---
plt.grid(True, axis='y', linestyle='--', alpha=0.7)
plt.yscale('log')
ax.yaxis.set_major_locator(ticker.LogLocator(base=10.0, subs=[1.0], numticks=6))
ax.yaxis.set_minor_locator(ticker.NullLocator())
ax.yaxis.set_major_formatter(
    ticker.FuncFormatter(lambda y, _: f"{int(y)}s" if y >= 1 else f"{y:.2f}s")
)
ax.set_yticklabels(ax.get_yticklabels(), fontsize=40)

# --- Add bar value labels ---
for i, (query_type, workload_order) in enumerate([(qt, wo) for qt in query_types for wo in workload_orders]):
    group_x = x_positions[i] - group_width/2 + bar_width/2 + x * bar_width
    for j, optimizer in enumerate(optimizers):
        plan_time = plan_data.loc[(query_type, workload_order)][optimizer]
        exec_time = exec_data.loc[(query_type, workload_order)][optimizer]
        total_time = plan_time + exec_time
        if total_time > 0:
            plt.text(group_x[j], total_time + (0.05 * total_time), 
                     f"{total_time:.0f}", 
                     ha='center', va='bottom', fontsize=38, rotation=90)

ax.margins(x=0.01)
# --- Save and show ---
output_dir = '/data/hdd1/users/kmparmp/Learned-Optimizers-Benchmarking-Suite/experiments/experiment2/plots'
if not os.path.exists(output_dir):
    os.makedirs(output_dir)
output_file = os.path.join(output_dir, 'combined_planning_execution_time.pdf')
plt.tight_layout(pad=0.0, w_pad=0.0)
plt.savefig(output_file, bbox_inches='tight')
plt.show()

/tmp/ipykernel_1692464/2564446480.py:175: UserWarning: FixedFormatter should only be used together with FixedLocator
  ax.set_yticklabels(ax.get_yticklabels(), fontsize=40)


## Takeaways

* **LERO** has the highest total latency due to its just-in-time candidate ranking and the need to disable PostgreSQL's built-in parallelism.
* **BAO** spends a lot of time planning (often more than executing), as it evaluates many hint combinations. However, it has the fastest execution time, so the planning overhead pays off.
* **PostgreSQL** (the traditional optimizer) is the most efficient overall—fast planning and execution, thanks to mature engineering and no ML inference steps.
* **LOGER** and **FASTgres** come close to PostgreSQL’s performance. However, FASTgres struggles when encountering entirely new queries (Base Query split), falling back to standard PostgreSQL plans without learned improvements.

**Training order matters**, especially for LOGER and LERO:

* LOGER does best when trained on simpler queries first (ascending complexity), and worst when trained based on ascending latency.
* LERO shows a similar pattern, though less strongly—random order actually works best.
* While BAO exhibits variations in performance per query ordering, it doesnt showcase a consistent pattern where a specific ordering performs better or worse than other query orderings per train-test split strategies. 
* FASTgres doesn't seem to be sensitive to the order of training queries.

It seems like training on simpler queries first helps models learn more effectively, while training based on latency seems to sometimes hurt performance.

**Disclaimer**: Models trained on the Base Query split might look good at first, but they were tested on fewer queries (19 vs. 22 or 33 in other splits). When you factor that in, their performance isn’t as strong—especially when faced with unfamiliar query templates.

## Workload Robustness

In [28]:
# import pandas as pd
# import seaborn as sns
# import matplotlib.pyplot as plt
# import numpy as np

# # Cases with high variation in execution time

# latency_stats = df.groupby(['optimizer', 'query_name', 'query_type', 'workload_order'])['execution_time'].agg(
#     mean='mean', std='std', min='min', max='max'
# ).reset_index()

# latency_stats['range'] = latency_stats['max'] - latency_stats['min']
# # latency_stats['cv'] = latency_stats['std'] / latency_stats['mean']

# unstable_queries = latency_stats.sort_values(by='range', ascending=False)
# print("Top unstable queries by CV:")

# # Export the top 20 unstable queries to a CSV file
# unstable_queries.head(20).to_csv(os.path.join(output_dir, 'unstable_queries.csv'), index=False)
# unstable_queries.head(20)

# Remove run1 entries
df_no_run1 = df[df['run'] != 1]

# Recompute stats without run1
latency_stats = df.groupby(['optimizer', 'query_name', 'query_type', 'workload_order'])['execution_time'].agg(
    mean='mean', std='std', min='min', max='max'
).reset_index()

latency_stats['range'] = latency_stats['max'] - latency_stats['min']
# latency_stats['cv'] = latency_stats['std'] / latency_stats['mean']

unstable_queries = latency_stats.sort_values(by='range', ascending=False)

print("Top unstable queries by CV (excluding run1):")
unstable_queries.head(20).to_csv(os.path.join(output_dir, 'unstable_queries.csv'), index=False)
unstable_queries.head(20)

# Do 2 seperate tables, one for NEO and one for the rest
df_neo = df[df['optimizer'] == 'NEO']
df_rest = df[df['optimizer'] != 'NEO']

latency_stats_neo = df_neo.groupby(['optimizer', 'query_name', 'query_type', 'workload_order'])['execution_time'].agg(
    mean='mean', std='std', min='min', max='max'
).reset_index()
latency_stats_rest = df_rest.groupby(['optimizer', 'query_name', 'query_type', 'workload_order'])['execution_time'].agg(
    mean='mean', std='std', min='min', max='max'
).reset_index()

latency_stats_neo['range'] = latency_stats_neo['max'] - latency_stats_neo['min']
latency_stats_rest['range'] = latency_stats_rest['max'] - latency_stats_rest['min']

unstable_queries_neo = latency_stats_neo.sort_values(by='range', ascending=False)
unstable_queries_rest = latency_stats_rest.sort_values(by='range', ascending=False)

Top unstable queries by CV (excluding run1):


In [29]:
print("Top unstable queries by CV (excluding run1) - NEO:")
unstable_queries_neo.head(5).to_csv(os.path.join(output_dir, 'unstable_queries_neo.csv'), index=False)
unstable_queries_neo.head(5)

Top unstable queries by CV (excluding run1) - NEO:


optimizer query_name     query_type        workload_order        mean  \
203       NEO         7c  leave_one_out     ascending_latency   39.120010   
66        NEO        20c  leave_one_out     ascending_latency   19.187927   
17        NEO        14a  leave_one_out                random   15.229170   
213       NEO         8c   random_split                random  217.326129   
211       NEO         8c   random_split  ascending_complexity  213.413009   

           std         min         max       range  
203  60.221049    4.278624  108.657237  104.378613  
66   25.599408    4.320502   48.747404   44.426902  
17   20.243995    3.536496   38.604921   35.068425  
213   5.590885  213.918636  223.778532    9.859896  
211   4.966063  208.900657  218.733625    9.832968

In [30]:
print("Top unstable queries by CV (excluding run1) - Rest:")
unstable_queries_rest.head(10).to_csv(os.path.join(output_dir, 'unstable_queries_rest.csv'), index=False)
unstable_queries_rest.head(10)

Top unstable queries by CV (excluding run1) - Rest:


optimizer query_name     query_type        workload_order       mean  \
140       BAO        30a  leave_one_out                random   5.227239   
880     LOGER         8c   random_split     ascending_latency  10.387343   
104       BAO        25c   random_split                random   6.522525   
103       BAO        25c   random_split     ascending_latency   6.468326   
106       BAO        26c  leave_one_out     ascending_latency   4.637386   
443  FASTgres         9c   random_split                random   2.136056   
40        BAO        17b   random_split     ascending_latency   5.894462   
18        BAO        15a     base_query  ascending_complexity   1.191980   
428  FASTgres         7c  leave_one_out                random   4.061455   
427  FASTgres         7c  leave_one_out     ascending_latency   4.348966   

          std       min        max     range  
140  3.037114  3.393352   8.732948  5.339596  
880  1.221805  9.298375  11.708627  2.410252  
104  1.184003  5.575535   7.849994  2.274459  
103  1.226771  5.755540   7.884870  2.129330  
106  1.148535  3.942330   5.963079  2.020749  
443  1.119876  1.413966   3.426112  2.012146  
40   0.935792  5.144972   6.943302  1.798330  
18   1.008725  0.561882   2.355415  1.793533  
428  0.856126  3.113528   4.778376  1.664848  
427  0.830980  3.462786   5.110713  1.647927

In [31]:
# import os
# import matplotlib.pyplot as plt
# import seaborn as sns
# import matplotlib.ticker as ticker

# plt.figure(figsize=(14, 6), dpi=600)
# sns.boxplot(data=df, x='optimizer', y='execution_time', hue='query_type')
# sns.set_theme(style="whitegrid")
# palette = sns.color_palette('Set2', n_colors=len(optimizers))
# # --- Logarithmic y-axis ---
# plt.yscale('log')

# # Major ticks only at powers of 10
# ax = plt.gca()
# ax.set_ylabel('')
# ax.set_xlabel('')
# ax.yaxis.set_major_locator(ticker.LogLocator(base=10.0, subs=[1.0], numticks=6))
# ax.yaxis.set_minor_locator(ticker.NullLocator())
# ax.yaxis.set_major_formatter(ticker.FuncFormatter(lambda y, _: f"{int(y)}s" if y >= 1 else f"{y:.2f}s"))

# plt.grid(True, axis='y', linestyle='--', alpha=0.7)

# # --- Legend above the plot ---
# plt.legend(
#     title='Query Type',
#     loc='upper center',
#     bbox_to_anchor=(0.5, 1.12),
#     ncol=len(df['query_type'].unique()),  # one column per query type
#     fontsize=9,
#     frameon=True,
#     facecolor='white',
#     edgecolor='black',
#     fancybox=True,
#     shadow=False
# )

# plt.xticks(rotation=0)
# plt.tight_layout(pad=0.01)

# # --- Save plot ---
# output_dir = '/data/hdd1/users/kmparmp/Learned-Optimizers-Benchmarking-Suite/experiments/experiment2/plots'
# if not os.path.exists(output_dir):
#     os.makedirs(output_dir)
# output_file = os.path.join(output_dir, 'execution_time_variability.png')
# plt.savefig(output_file, bbox_inches='tight', dpi=600)
# plt.show()

### Takeaways

* **LERO** is by far the least stable—responsible for 11 of the top 20 most variable cases. Some of its queries (like 20a and 25c) show huge swings in runtime, which is also depicted with various outliers in the figure

* **BAO** appears in 6 of the top 20, but its variation is much lower (CVs around 1.0).

* **LOGER** shows up 3 times. Only one of those (Query 15b) has high variability, while the others are fairly stable—suggesting it’s more consistent overall, though not immune to occasional instability.

* **PostgreSQL** doesn’t appear at all in the high-variance list, confirming its stable and deterministic behavior. **FASTgres** is also ommited from the table indicating the robustness in its performance.